In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import odeint
import panel as pn
from bokeh.plotting import figure, output_notebook, show
import colorcet
colors = colorcet.b_glasbey_category10
pn.extension()

output_notebook()
# X signals
def X_signal(t, t_start_x, duration_x):
    return 1.0 if t_start_x <= t < t_start_x + duration_x else 0.0

# Y signals
def Y_signal(t, t_start_y, duration_y):
    if t < t_start_y:
        return -1
    if  t_start_y <= t < t_start_y + duration_y:
        return 1
    else:
        return 0  
    # return -1

# A signals
def A_signal(t, t_start_a, duration_a):
    if t < t_start_a:
        return -1
    if  t_start_a <= t < t_start_a + duration_a:
        return 1
    else:
        return 0  
    # return -1

def ffl(by, kxy, ay, bz, kxz, kyz, az, h, type, logic, X, Y, Z, Sy):
    # logic = '1' if AND, logic = '-1' if OR
    threshold_y = 0.5
    Y_a = Y if Sy == 1 else 0
    if logic == 1: #

        if type == 1:
            # if Sy == -1:
            #     dY = 0
            # elif Sy == 1:
            #     dY = by * reg(X, kxy, h, 1) - ay * Y
            # else: 
            #     dY = -ay * Y
            dY = by * reg(X, kxy, h, 1) - ay * Y 
            # dY = by * reg(X, kxy, h, 1) - ay * Y
            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, 1) * reg(Y_a, kyz, h, 1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ =  - az * Z
            else:
                dZ = 0

        if type == 2:
            # dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            dY = by * reg(X, kxy, h, -1) - ay * Y 

            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, -1) * reg(Y_a, kyz, h, 1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0
        
        if type == 3:
            dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, -1) * reg(Y, kyz, h, -1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

        if type == 4:
            dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, 1) * reg(Y, kyz, h, -1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0
        
        if type == 5:
            dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, 1) * reg(Y, kyz, h, -1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0
        
        if type == 6:
            dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, -1) * reg(Y, kyz, h, -1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0
        
        if type == 7:
            dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, -1) * reg(Y, kyz, h, 1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0
        
        if type == 8:
            dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * reg(X, kxz, h, 1) * reg(Y, kyz, h, 1) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

    else: 

        if type == 1:
            dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0
        
        if type == 2:
            dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

        if type == 3:
            dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

        if type == 4:
            dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

        if type == 5:
            dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

        if type == 6:
            dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

        if type == 7:
            dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0

        if type == 8:
            dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
            if Y >= threshold_y:
                dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
            elif Y <= threshold_y and Z >= 0:
                dZ = - az * Z
            else:
                dZ = 0
    
    return [dY, dZ]




# define regulaiton funcitons
def reg(u, k, h, pattern):
    '''
    AND-logic regulation function
    u: input signal
    k: regulation coeficient
    h: hill coefficient
    pattern: 'activation' or 'repression' ==> '1' or '-1'
    '''
    if pattern == 1:
        return (u/k)**h / (1 + (u/k)**h)
    elif pattern == -1:
        return 1 / (1 + (u/k)**h)
    else:
        raise ValueError('pattern must be 1 or -1')

def reg_or(u, k_u, k_v, v, h, pattern):
    '''
    OR-logic regulation function
    k_xz: regulation coeficient
    k_yz: regulation coeficient
    pattern: 'activation' or 'repression' ==> '1' or '-1'
    '''
    if pattern == 1:
        return ((u/k_u)**h) / (1 + (u/k_u)**h + (v/k_v)**h)
    elif pattern == -1:
        return 1 / (1 + (u/k_u)**h + (v/k_v)**h)
    else:
        raise ValueError('pattern must be 1 or -1')


def kinetics(variables, t, para):
    # Y, Z = variables
    by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a = para
    Y, Z, A, B = variables
    X = X_signal(t, t_start_x, duration_x)
    Sy = Y_signal(t, t_start_y, duration_y)
    Sa = A_signal(t, t_start_a, duration_a)

    # logic = '1' if AND, logic = '-1' if OR
    # if logic == 1: #

    #     if type == 1:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         # dY = by * reg(X, kxy, h, 1) - ay * Y
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, 1) * reg(Y, kyz, h, 1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ =  - az * Z
    #         else:
    #             dZ = 0

    #     if type == 2:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, -1) * reg(Y, kyz, h, 1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0
        
    #     if type == 3:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, -1) * reg(Y, kyz, h, -1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    #     if type == 4:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, 1) * reg(Y, kyz, h, -1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0
        
    #     if type == 5:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, 1) * reg(Y, kyz, h, -1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0
        
    #     if type == 6:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, -1) * reg(Y, kyz, h, -1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0
        
    #     if type == 7:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, -1) * reg(Y, kyz, h, 1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0
        
    #     if type == 8:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * reg(X, kxz, h, 1) * reg(Y, kyz, h, 1) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    # else: 

    #     if type == 1:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0
        
    #     if type == 2:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    #     if type == 3:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    #     if type == 4:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    #     if type == 5:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    #     if type == 6:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, -1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    #     if type == 7:
    #         dY = by * reg(X, kxy, h, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, -1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    #     if type == 8:
    #         dY = by * reg(X, kxy, h, -1) - ay * Y if (Sy == 1 or Sy == 0) else 0
    #         if Y >= threshold_y:
    #             dZ = bz * (reg_or(X, kxz, kyz, Y, h, 1) + reg_or(Y, kyz, kxz, X, h, 1)) - az * Z
    #         elif Y <= threshold_y and Z >= 0:
    #             dZ = - az * Z
    #         else:
    #             dZ = 0

    dY, dZ = ffl(by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, X, Y, Z, Sy)
    dA, dB = ffl(ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, Z, A, B, Sa)
    # dA, dB = ffl(ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, Y, A, B, Sa)


    # dA = 1 * reg(Z, 0.1, 2, 1) - 1 * A if (Sa == 1 or Sa == 0) else 0
    # if A >= 0.5:
    #         dB = 1 * reg(Z, 0.1, 2, 1) * reg(A, 0.5, 2, 1) - 1 * B
    # elif A <= 0.5 and B >= 0:
    #         dB = - 1 * B
    # else:
    #         dB = 0

    return [dY, dZ, dA, dB]

def feedforward_loop_scipy(t_end, para, 
                        #    duration, 
                        #    threshold_y,
                           ):
    timesteps = np.linspace(0, t_end, num=50000)
    # initial_conditions = [0.0, 0.0]
    # initial_conditions = [0.0, 0.0]
    initial_conditions = [0,0,0,0]

    # params = (duration, threshold_y, para)
    params = (para,)
    # by, kxy, ay, bz, kxz, kyz, az, h, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h, type_2, logic_2 ,t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a = para
    by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a = para

    result = odeint(kinetics, initial_conditions, timesteps, args=params)
    X = np.array([X_signal(t, t_start_x, duration_x) for t in timesteps])
    return timesteps, X, result[:, 0], result[:, 1], result[:, 2], result[:, 3]

t_end = 50
para_dict = {'by':1, 'kxy':0.1, 'ay':1, 'bz':1, 'kxz':0.1, 'kyz':0.5, 'az':1, 'h_1':2, 'type_1':1, 'logic_1' : 1, 
             'ba':1, 'kza':0.1, 'aa':1, 'bb':1, 'kzb':0.1, 'kab':0.5, 'ab':1, 'h_2':2, 'type_2':1, 'logic_2' : 1,
             't_start_x' : 10, 'duration_x': 15,
             't_start_y' : 10, 'duration_y' :20,
             't_start_a' : 15, 'duration_a': 10}
para = list(para_dict.values())
print(para)
# duration = 20
# threshold_y = 0.5

time, X, Y, Z, A, B = feedforward_loop_scipy(t_end, para)


p = figure(
   tools="pan,box_zoom,reset,save",
   y_axis_type="linear", y_range=[0, 2], title="FFL",
   x_axis_label='sections', y_axis_label='concentration'
)

p.line(time, X, legend_label="X", line_width=2.2, line_color=colors[0])
p.line(time, Y, legend_label="Y", line_width=2.2, line_color=colors[1])
p.line(time, Z, legend_label="Z", line_width=2.2, line_color=colors[2])
p.line(time, A, legend_label="A", line_width=2.2, line_color=colors[3])
p.line(time, B, legend_label="B", line_width=2.2, line_color=colors[4])

show(p)


# plt.plot(time, X, label="X")
# plt.plot(time, Y, label="Y")
# plt.plot(time, Z, label="Z")
# plt.xlabel("Time")
# plt.ylabel("Concentration")
# plt.legend()
# plt.show()

Loading BokehJS ...

[1, 0.1, 1, 1, 0.1, 0.5, 1, 2, 1, 1, 1, 0.1, 1, 1, 0.1, 0.5, 1, 2, 1, 1, 10, 15, 10, 20, 15, 10]


In [2]:
# dash board building
# parameters : para_dict = {'by':1, 'kxy':0.1, 'ay':1, 'bz':1, 'kxz':0.1, 'kyz':0.5, 'az':1, 'h':1, 'type':2}
# by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a = para
import panel as pn
from bokeh.plotting import figure, output_notebook, show
import colorcet 
colors = colorcet.b_glasbey_category10
# pn.extension(comms="vscode")
pn.extension()

output_notebook()

alpha_param_sliders_kwargs = dict(start=0, end=2, step=0.1, value=1)
beta_param_sliders_kwargs = dict(start=0, end=2, step=0.1, value=1)
k_param_sliders_kwargs = dict(start=0, end=5, step=0.1, value=0.1)
hill_coeff_kwags = dict(start=1, end=10, step=0.1, value=2)

beta_y_slider = pn.widgets.FloatSlider(name="β_y", **beta_param_sliders_kwargs)
beta_z_slider = pn.widgets.FloatSlider(name="β_z", **beta_param_sliders_kwargs)
beta_a_slider = pn.widgets.FloatSlider(name="β_a", **beta_param_sliders_kwargs)
beta_b_slider = pn.widgets.FloatSlider(name="β_b", **beta_param_sliders_kwargs)


# alpha_y_slider = pn.widgets.FloatSlider(name="γ", **param_sliders_kwargs)
alpha_y_slider = pn.widgets.FloatSlider(name=u"\u03b1y", **alpha_param_sliders_kwargs)
alpha_z_slider = pn.widgets.FloatSlider(name=u"\u03b1z", **alpha_param_sliders_kwargs)
alpha_a_slider = pn.widgets.FloatSlider(name=u"\u03b1a", **alpha_param_sliders_kwargs)
alpha_b_slider = pn.widgets.FloatSlider(name=u"\u03b1b", **alpha_param_sliders_kwargs)

k_xy_slider = pn.widgets.FloatSlider(name="k_xy", **k_param_sliders_kwargs)
k_xz_slider = pn.widgets.FloatSlider(name="k_xz", **k_param_sliders_kwargs)
k_yz_slider = pn.widgets.FloatSlider(name="k_yz", **k_param_sliders_kwargs)
k_za_slider = pn.widgets.FloatSlider(name="k_za", **k_param_sliders_kwargs)
k_zb_slider = pn.widgets.FloatSlider(name="k_zb", **k_param_sliders_kwargs)
k_ab_slider = pn.widgets.FloatSlider(name="k_ab", **k_param_sliders_kwargs)

h_slider_1 = pn.widgets.FloatSlider(name="hill coefficent", **hill_coeff_kwags)
h_slider_2 = pn.widgets.FloatSlider(name="hill coefficent", **hill_coeff_kwags)

type_slider_1 = pn.widgets.FloatSlider(name="type_1", start=1, end=8, step=1, value=1)
type_slider_2 = pn.widgets.FloatSlider(name="type_2", start=1, end=8, step=1, value=1)

logic_selector_1 = pn.widgets.RadioBoxGroup(name = 'Logic', options={'AND':1, 'OR':-1}, inline=True)
logic_selector_2 = pn.widgets.RadioBoxGroup(name = 'Logic', options={'AND':1, 'OR':-1}, inline=True)

t_start_x_slider = pn.widgets.FloatSlider(name="t_start_Sx", start=0, end=100, step=1, value=10)
t_start_y_slider = pn.widgets.FloatSlider(name="t_start_Sy", start=0, end=100, step=1, value=10)
t_start_a_slider = pn.widgets.FloatSlider(name="t_start_Sa", start=0, end=100, step=1, value=15)

duration_x_slider = pn.widgets.FloatSlider(name="duration_Sx", start=0, end=100, step=1, value=10)
duration_y_slider = pn.widgets.FloatSlider(name="duration_Sy", start=0, end=100, step=1, value=10)
duration_a_slider = pn.widgets.FloatSlider(name="duration_Sa", start=0, end=100, step=1, value=10)

show_x_selector = pn.widgets.Checkbox(name="show_x", value=True)
show_y_selector = pn.widgets.Checkbox(name="show_y", value=True)
show_z_selector = pn.widgets.Checkbox(name="show_z", value=True)
show_a_selector = pn.widgets.Checkbox(name="show_a", value=False)
show_b_selector = pn.widgets.Checkbox(name="show_b", value=False)



# duration_x t_start_y, duration_y, t_start_a, duration_




Loading BokehJS ...

In [6]:
# by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a = para
import panel as pn
@pn.depends(
    beta_y_slider.param.value,
    k_xy_slider.param.value,
    alpha_y_slider.param.value,
    beta_z_slider.param.value,
    k_xz_slider.param.value,
    k_yz_slider.param.value,
    alpha_z_slider.param.value,
    h_slider_1.param.value,
    type_slider_1.param.value,
    logic_selector_1.param.value,
    beta_a_slider.param.value,
    k_za_slider.param.value,
    alpha_a_slider.param.value,
    beta_b_slider.param.value,
    k_zb_slider.param.value,    
    k_ab_slider.param.value,
    alpha_b_slider.param.value,
    h_slider_2.param.value,
    type_slider_2.param.value,
    logic_selector_2.param.value,
    t_start_x_slider.param.value,
    duration_x_slider.param.value,
    t_start_y_slider.param.value,
    duration_y_slider.param.value,
    t_start_a_slider.param.value,
    duration_a_slider.param.value,
    show_x_selector.param.value,
    show_y_selector.param.value,
    show_z_selector.param.value,
    show_a_selector.param.value,
    show_b_selector.param.value,
)
def plot_ffl(
    by,
    kxy,
    ay,
    bz,
    kxz,
    kyz,
    az,
    h_1,
    type_1,
    logic_1, 
    ba, 
    kza, 
    aa, 
    bb, 
    kzb, 
    kab, 
    ab, 
    h_2, 
    type_2, 
    logic_2, 
    t_start_x, 
    duration_x, 
    t_start_y, 
    duration_y, 
    t_start_a, 
    duration_a,
    show_x,
    show_y,
    show_z,
    show_a,
    show_b,
    # t_end=50,
    # duration=20,
    # threshold_y=0.5,
):
    para = [by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a]
    # t_end = 35
    # duration = 20
    # threshold_y = 0.5
    time, X, Y, Z, A, B = feedforward_loop_scipy(t_end, para)
    if type_1 <= 4:
        title_1 = f"C{type_1}-FFL"
    else:
        title_1 = f"I{type_1-4}-FFL"
    if type_2 <= 4:
        title_2 = f"C{type_2}-FFL"
    else:
        title_2 = f"I{type_2-4}-FFL"

    if show_a==False and show_b==False:
        title_f = f"Dynamic change of concentration under {title_1}"
    else: 
        title_f = f"Dynamic change of concentration under {title_1} and second {title_2}"

    p = figure(
        tools="pan,box_zoom,reset,save",
        y_axis_type="linear",
        y_range=[0, 1.5],
        # title=f"Dynamic change of concentration under {title_1} and second {title_2}",
        # title=f"Dynamic change of concentration under {title_1} and second {title_2}",
        # title=title_f + f'\nSx: from {t_start_x}s to {t_start_x + duration_x}s'+f'\nSy: from {t_start_y}s to {t_start_y + duration_y}s ' + f'\nSa: from {t_start_a}s to {t_start_a + duration_a}s',
        title=title_f + f'\nSx: from {t_start_x}s to {t_start_x + duration_x}s'+f'\nSy: from {t_start_y}s to {t_start_y + duration_y}s ',
        x_axis_label="time",
        y_axis_label="concentration",
    )

    # p.line(time, X, legend_label="X", line_width=2.2, line_color=colors[0])
    # p.line(time, Y, legend_label="Y", line_width=2.2, line_color=colors[1])
    # p.line(time, Z, legend_label="Z", line_width=2.2, line_color=colors[2])
    # p.line(time, A, legend_label="A", line_width=2.2, line_color=colors[3])
    # p.line(time, B, legend_label="B", line_width=2.2, line_color=colors[4])

    p.line(time, X, legend_label="X", line_width=2.2, line_color=colors[0]) if show_x else None
    p.line(time, Y, legend_label="Y", line_width=2.2, line_color=colors[1]) if show_y else None
    p.line(time, Z, legend_label="Z", line_width=2.2, line_color=colors[2]) if show_z else None
    p.line(time, A, legend_label="A", line_width=2.2, line_color=colors[3]) if show_a else None
    p.line(time, B, legend_label="B", line_width=2.2, line_color=colors[4]) if show_b else None

    return p

In [7]:
sliders = pn.Row(
    pn.Spacer(width=30),
    pn.Column(beta_y_slider, beta_z_slider, beta_a_slider, beta_b_slider, alpha_y_slider, alpha_z_slider, alpha_a_slider, alpha_b_slider, width=150),
    pn.Spacer(width=10),
    # pn.Column(alpha_y_slider, alpha_z_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(k_xy_slider, k_xz_slider, k_yz_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(k_za_slider, k_zb_slider, k_ab_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(h_slider_1, h_slider_2, type_slider_1, type_slider_2, width=150),
    pn.Spacer(width=10),
    pn.Column(logic_selector_1, logic_selector_2, 
              show_x_selector, 
              show_y_selector,
              show_z_selector,
              show_a_selector,
              show_b_selector,
              width=150),
    pn.Spacer(width=10),
    pn.Column(t_start_x_slider, t_start_y_slider, t_start_a_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(duration_x_slider, duration_y_slider, duration_a_slider, width=150),
)



In [8]:
pn.Column(
    plot_ffl,
    pn.Spacer(width=10),
    pn.Row(sliders, pn.Spacer(width=10)),
    # pn.bind(plot_ffl, sliders),

)

BokehModel(combine_events=True, render_bundle={'docs_json': {'10472b60-2822-4a8e-a081-98871532c6a7': {'defs': …

In [6]:
# by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a = para
import panel as pn
@pn.depends(
    beta_y_slider.param.value,
    k_xy_slider.param.value,
    alpha_y_slider.param.value,
    beta_z_slider.param.value,
    k_xz_slider.param.value,
    k_yz_slider.param.value,
    alpha_z_slider.param.value,
    h_slider_1.param.value,
    type_slider_1.param.value,
    logic_selector_1.param.value,
    beta_a_slider.param.value,
    k_za_slider.param.value,
    alpha_a_slider.param.value,
    beta_b_slider.param.value,
    k_zb_slider.param.value,    
    k_ab_slider.param.value,
    alpha_b_slider.param.value,
    h_slider_2.param.value,
    type_slider_2.param.value,
    logic_selector_2.param.value,
    t_start_x_slider.param.value,
    duration_x_slider.param.value,
    t_start_y_slider.param.value,
    duration_y_slider.param.value,
    t_start_a_slider.param.value,
    duration_a_slider.param.value,
    show_x_selector.param.value,
    show_y_selector.param.value,
    show_z_selector.param.value,
    show_a_selector.param.value,
    show_b_selector.param.value,
)
def plot_phase(
    by,
    kxy,
    ay,
    bz,
    kxz,
    kyz,
    az,
    h_1,
    type_1,
    logic_1, 
    ba, 
    kza, 
    aa, 
    bb, 
    kzb, 
    kab, 
    ab, 
    h_2, 
    type_2, 
    logic_2, 
    t_start_x, 
    duration_x, 
    t_start_y, 
    duration_y, 
    t_start_a, 
    duration_a,
    show_x,
    show_y,
    show_z,
    show_a,
    show_b,
    # t_end=50,
    # duration=20,
    # threshold_y=0.5,
):
    para = [by, kxy, ay, bz, kxz, kyz, az, h_1, type_1, logic_1, ba, kza, aa, bb, kzb, kab, ab, h_2, type_2, logic_2, t_start_x, duration_x, t_start_y, duration_y, t_start_a, duration_a]
    # t_end = 35
    # duration = 20
    # threshold_y = 0.5
    time, X, Y, Z, A, B = feedforward_loop_scipy(t_end, para)
    if type_1 <= 4:
        title_1 = f"C{type_1}-FFL"
    else:
        title_1 = f"I{type_1-4}-FFL"
    if type_2 <= 4:
        title_2 = f"C{type_2}-FFL"
    else:
        title_2 = f"I{type_2-4}-FFL"

    if show_a==False and show_b==False:
        title_f = f"Dynamic change of concentration under {title_1}"
    else: 
        title_f = f"Dynamic change of concentration under {title_1} and second {title_2}"

    p = figure(
        tools="pan,box_zoom,reset,save",
        y_axis_type="linear",
        y_range=[0, 1.5],
        # title=f"Dynamic change of concentration under {title_1} and second {title_2}",
        # title=f"Dynamic change of concentration under {title_1} and second {title_2}",
        # title=title_f + f'\nSx: from {t_start_x}s to {t_start_x + duration_x}s'+f'\nSy: from {t_start_y}s to {t_start_y + duration_y}s ',
        title = f'Phase space analysis',
        x_axis_label="Z",
        y_axis_label="A",
    )

    # p.line(time, X, legend_label="X", line_width=2.2, line_color=colors[0])
    # p.line(time, Y, legend_label="Y", line_width=2.2, line_color=colors[1])
    # p.line(time, Z, legend_label="Z", line_width=2.2, line_color=colors[2])
    # p.line(time, A, legend_label="A", line_width=2.2, line_color=colors[3])
    # p.line(time, B, legend_label="B", line_width=2.2, line_color=colors[4])

    # p.line(time, X, legend_label="X", line_width=2.2, line_color=colors[0]) if show_x else None
    # p.line(time, Y, legend_label="Y", line_width=2.2, line_color=colors[1]) if show_y else None
    # p.line(time, Z, legend_label="Z", line_width=2.2, line_color=colors[2]) if show_z else None
    # p.line(time, A, legend_label="A", line_width=2.2, line_color=colors[3]) if show_a else None
    # p.line(time, B, legend_label="B", line_width=2.2, line_color=colors[4]) if show_b else None
    p.line(B, Z, legend_label="phase", line_width=2.2, line_color=colors[0]) 
    return p

In [7]:
sliders = pn.Row(
    pn.Spacer(width=30),
    pn.Column(beta_y_slider, beta_z_slider, beta_a_slider, beta_b_slider, alpha_y_slider, alpha_z_slider, alpha_a_slider, alpha_b_slider, width=150),
    pn.Spacer(width=10),
    # pn.Column(alpha_y_slider, alpha_z_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(k_xy_slider, k_xz_slider, k_yz_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(k_za_slider, k_zb_slider, k_ab_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(h_slider_1, h_slider_2, type_slider_1, type_slider_2, width=150),
    pn.Spacer(width=10),
    pn.Column(logic_selector_1, logic_selector_2, 
              show_x_selector, 
              show_y_selector,
              show_z_selector,
              show_a_selector,
              show_b_selector,
              width=150),
    pn.Spacer(width=10),
    pn.Column(t_start_x_slider, t_start_y_slider, t_start_a_slider, width=150),
    pn.Spacer(width=10),
    pn.Column(duration_x_slider, duration_y_slider, duration_a_slider, width=150),
)


In [8]:
pn.Column(
    plot_phase,
    pn.Spacer(width=10),
    pn.Row(sliders, pn.Spacer(width=10)),
)

BokehModel(combine_events=True, render_bundle={'docs_json': {'81badc07-19ae-424c-8527-3f355ee47939': {'defs': …

AttributeError: 'NoneType' object has no attribute 'lookup'

AttributeError: 'NoneType' object has no attribute 'lookup'

AttributeError: 'NoneType' object has no attribute 'lookup'

AttributeError: 'NoneType' object has no attribute 'lookup'

AttributeError: 'NoneType' object has no attribute 'lookup'

AttributeError: 'NoneType' object has no attribute 'lookup'

In [9]:
def time_to_half_steady_state(Y, Z):
    # diff_Y = np.diff(Y[:1000])
    # diff_Z = np.diff(Z)
    print(len(Y))
    # print(len(diff_Y))
    for i in range(len(Y)):
        if Y[i] >= 0.5 * max(Y):
            return ((i + 1) / 5000) * 50
    return -1  # return -1 if the system never returns to steady state

threshold_Y = 0.000001 * max(Y)
time_to_ss = time_to_half_steady_state(Y, Z)
print(f'Time to return to steady state:{time_to_ss}s')


50000
Time to return to steady state:106.94s


In [58]:
def kinetics_two_ffls(variables, t, duration, threshold_y, threshold_a, para):
    Y, Z, A, B = variables
    X = X_signal(t, duration)
    Sy = Y_signal(t, duration)
    Sa = A_signal(t, duration)  # assume A has its own signal, like Y
    by, kxy, ay, bz, kxz, kyz, az, h1, type1, ba, kza, aa, bb, kzb, kab, ab, h2, type2 = para

    # First FFL
    if type1 == 1:
        dY = by * reg(X, kxy, h1, 1) - ay * Y if (Sy == 1 or Sy == 0) else 0
        if Y >= threshold_y:
            dZ = bz * reg(X, kxz, h1, 1) * reg(Y, kyz, h1, 1) - az * Z
        elif Y <= threshold_y and Z >= 0:
            dZ = - az * Z
        else:
            dZ = 0

    # Second FFL
    if type2 == 1:
        dA = ba * reg(Z, kza, h2, 1) - aa * A if (Sa == 1 or Sa == 0) else 0
        if A >= threshold_a:
            dB = bb * reg(Z, kzb, h2, 1) * reg(A, kab, h2, 1) - ab * B
        elif A <= threshold_a and B >= 0:
            dB = - ab * B
        else:
            dB = 0

    return [dY, dZ, dA, dB]

def feedforward_loops_scipy(t_end, para, duration, threshold_y, threshold_a):
    timesteps = np.linspace(0, t_end, num=1000)
    initial_conditions = [0.0, 0.0, 0.0, 0.0]  # Y, Z, A, B

    params = (duration, threshold_y, threshold_a, para)

    result = odeint(kinetics_two_ffls, initial_conditions, timesteps, args=params)
    X = np.array([X_signal(t, duration) for t in timesteps])
    return timesteps, X, result[:, 0], result[:, 1], result[:, 2], result[:, 3]

t_end = 50
para_dict = {
    'by':1, 'kxy':0.1, 'ay':1, 'bz':1, 'kxz':0.1, 'kyz':0.6, 'az':1, 'h1':2, 'type1':1,
    'ba':1, 'kza':0.1, 'aa':1, 'bb':1, 'kzb':0.1, 'kab':0.6, 'ab':1, 'h2':2, 'type2':1
}
para = list(para_dict.values())
print(para)
duration = 20
threshold_y = 0.5
threshold_a = 0.5

time, X, Y, Z, A, B = feedforward_loops_scipy(t_end, para, duration, threshold_y, threshold_a)

p = figure(
    tools="pan,box_zoom,reset,save",
    y_axis_type="linear", y_range=[0, 2], title="FFL",
    x_axis_label='sections', y_axis_label='concentration'
)

p.line(time, X, legend_label="X", line_width=2.2, line_color=colors[0])
p.line(time, Y, legend_label="Y", line_width=2.2, line_color=colors[1])
p.line(time, Z, legend_label="Z", line_width=2.2, line_color=colors[2])
p.line(time, A, legend_label="A", line_width=2.2, line_color=colors[3])
p.line(time, B, legend_label="B", line_width=2.2, line_color=colors[4])
show(p)


[1, 0.1, 1, 1, 0.1, 0.6, 1, 2, 1, 1, 0.1, 1, 1, 0.1, 0.6, 1, 2, 1]


In [6]:
check = pn.widgets.Checkbox(name='Check me!', value=True)
check

ValueError: Boolean parameter 'value' must be True or False, not 1.